In [7]:
from pathlib import Path

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import sklearn
import ydata_profiling
from skrub import TableReport

In [2]:
data = pd.read_parquet(Path("data") / "train.parquet")
data.head()

counter_id              counter_name    site_id  \
48321  100007049-102007049  28 boulevard Diderot E-O  100007049   
48324  100007049-102007049  28 boulevard Diderot E-O  100007049   
48327  100007049-102007049  28 boulevard Diderot E-O  100007049   
48330  100007049-102007049  28 boulevard Diderot E-O  100007049   
48333  100007049-102007049  28 boulevard Diderot E-O  100007049   

                  site_name  bike_count                date  \
48321  28 boulevard Diderot         0.0 2020-09-01 02:00:00   
48324  28 boulevard Diderot         1.0 2020-09-01 03:00:00   
48327  28 boulevard Diderot         0.0 2020-09-01 04:00:00   
48330  28 boulevard Diderot         4.0 2020-09-01 15:00:00   
48333  28 boulevard Diderot         9.0 2020-09-01 18:00:00   

      counter_installation_date         coordinates counter_technical_id  \
48321                2013-01-18  48.846028,2.375429          Y2H15027244   
48324                2013-01-18  48.846028,2.375429          Y2H15027244   
48327                2013-01-18  48.846028,2.375429          Y2H15027244   
48330                2013-01-18  48.846028,2.375429          Y2H15027244   
48333                2013-01-18  48.846028,2.375429          Y2H15027244   

        latitude  longitude  log_bike_count  
48321  48.846028   2.375429        0.000000  
48324  48.846028   2.375429        0.693147  
48327  48.846028   2.375429        0.000000  
48330  48.846028   2.375429        1.609438  
48333  48.846028   2.375429        2.302585

In [3]:
external_conditions = pd.read_csv('data/external_data.csv')
external_conditions.head()

numer_sta                 date    pmer  tend  cod_tend   dd   ff       t  \
0       7149  2021-01-01 00:00:00  100810    80         1  270  1.8  272.75   
1       7149  2021-01-01 03:00:00  100920   110         3  300  1.7  271.25   
2       7149  2021-01-01 06:00:00  100950    30         3  290  2.6  271.95   
3       7149  2021-01-01 09:00:00  101100   150         2  280  1.7  272.45   
4       7149  2021-01-01 12:00:00  101110    30         0   50  1.0  276.95   

       td   u  ...  hnuage1  nnuage2  ctype2  hnuage2  nnuage3  ctype3  \
0  272.15  96  ...    600.0      NaN     NaN      NaN      NaN     NaN   
1  270.95  98  ...   1500.0      2.0     3.0   3000.0      NaN     NaN   
2  271.65  98  ...    480.0      4.0     6.0   2000.0      6.0     3.0   
3  272.05  97  ...   1740.0      3.0     3.0   2800.0      NaN     NaN   
4  274.15  82  ...    330.0      4.0     6.0    570.0      7.0     6.0   

   hnuage3  nnuage4  ctype4  hnuage4  
0      NaN      NaN     NaN      NaN  
1      NaN      NaN     NaN      NaN  
2   3000.0      NaN     NaN      NaN  
3      NaN      NaN     NaN      NaN  
4    810.0      NaN     NaN      NaN  

[5 rows x 59 columns]

In [10]:
# Dictionary mapping column names to their practical explanations
column_name_mapping = {
    'numer_sta': 'Station Number',
    'date': 'Date and Time',
    'pmer': 'Sea Level Pressure (hPa)',
    'tend': 'Pressure Tendency (hPa/3h)',
    'cod_tend': 'Pressure Tendency Code',
    'dd': 'Wind Direction (°)',
    'ff': 'Wind Speed (m/s)',
    't': 'Air Temperature (°C)',
    'td': 'Dew Point Temperature (°C)',
    'u': 'Relative Humidity (%)',
    'vv': 'Visibility (m)',
    'ww': 'Present Weather Code',
    'w1': 'Past Weather Code 1',
    'w2': 'Past Weather Code 2',
    'n': 'Total Cloud Cover (oktas)',
    'nbas': 'Cloud Base Height (m)',
    'hbas': 'Lowest Cloud Base Height (m)',
    'cl': 'Low Cloud Type',
    'cm': 'Medium Cloud Type',
    'ch': 'High Cloud Type',
    'pres': 'Station Level Pressure (hPa)',
    'niv_bar': 'Barometer Altitude (m)',
    'geop': 'Geopotential Height (m)',
    'tend24': '24h Pressure Tendency (hPa)',
    'tn12': '12h Minimum Temperature (°C)',
    'tn24': '24h Minimum Temperature (°C)',
    'tx12': '12h Maximum Temperature (°C)',
    'tx24': '24h Maximum Temperature (°C)',
    'tminsol': 'Minimum Soil Temperature (°C)',
    'sw': 'Sunshine Duration (hours)',
    'tw': 'Wet Bulb Temperature (°C)',
    'raf10': '10min Max Wind Gust (m/s)',
    'rafper': 'Max Wind Gust (m/s)',
    'per': 'Measurement Period Duration',
    'etat_sol': 'Ground State',
    'ht_neige': 'Snow Height (cm)',
    'ssfrai': 'New Snow Depth (cm)',
    'perssfrai': 'New Snowfall Duration (hours)',
    'rr1': 'Rainfall (1h, mm)',
    'rr3': 'Rainfall (3h, mm)',
    'rr6': 'Rainfall (6h, mm)',
    'rr12': 'Rainfall (12h, mm)',
    'rr24': 'Rainfall (24h, mm)',
    'phenspe1': 'Special Weather Phenomenon 1',
    'phenspe2': 'Special Weather Phenomenon 2',
    'phenspe3': 'Special Weather Phenomenon 3',
    'phenspe4': 'Special Weather Phenomenon 4',
    'nnuage1': 'Layer 1 Cloud Cover (oktas)',
    'ctype1': 'Layer 1 Cloud Type',
    'hnuage1': 'Layer 1 Cloud Base Height (m)',
    'nnuage2': 'Layer 2 Cloud Cover (oktas)',
    'ctype2': 'Layer 2 Cloud Type',
    'hnuage2': 'Layer 2 Cloud Base Height (m)',
    'nnuage3': 'Layer 3 Cloud Cover (oktas)',
    'ctype3': 'Layer 3 Cloud Type',
    'hnuage3': 'Layer 3 Cloud Base Height (m)',
    'nnuage4': 'Layer 4 Cloud Cover (oktas)',
    'ctype4': 'Layer 4 Cloud Type',
    'hnuage4': 'Layer 4 Cloud Base Height (m)',
}

# Rename columns in the DataFrame
external_conditions = external_conditions.rename(columns=column_name_mapping)


In [12]:
threshold = len(external_conditions) * 0.8
external_conditions = external_conditions.loc[:, external_conditions.isnull().sum() < threshold]
TableReport(external_conditions)

Processing column  42 / 42


<TableReport: use .open() to display>

In [13]:
# Convert 'Date and Time' column in external_conditions to datetime
external_conditions['Date and Time'] = pd.to_datetime(external_conditions['Date and Time'])

# Merge the dataframes
merged_data = pd.merge(data, external_conditions, left_on='date', right_on='Date and Time', how='inner')

# Display the merged dataframe
merged_data.head()

/var/folders/95/xl50cbyd26j4ngz698y18j3m0000gn/T/ipykernel_89349/3982021310.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  external_conditions['Date and Time'] = pd.to_datetime(external_conditions['Date and Time'])


counter_id              counter_name    site_id  \
0  100007049-102007049  28 boulevard Diderot E-O  100007049   
1  100007049-102007049  28 boulevard Diderot E-O  100007049   
2  100007049-102007049  28 boulevard Diderot E-O  100007049   
3  100007049-102007049  28 boulevard Diderot E-O  100007049   
4  100007049-102007049  28 boulevard Diderot E-O  100007049   

              site_name  bike_count                date  \
0  28 boulevard Diderot         1.0 2020-09-01 03:00:00   
1  28 boulevard Diderot         4.0 2020-09-01 15:00:00   
2  28 boulevard Diderot         9.0 2020-09-01 18:00:00   
3  28 boulevard Diderot         7.0 2020-09-02 18:00:00   
4  28 boulevard Diderot        12.0 2020-09-03 15:00:00   

  counter_installation_date         coordinates counter_technical_id  \
0                2013-01-18  48.846028,2.375429          Y2H15027244   
1                2013-01-18  48.846028,2.375429          Y2H15027244   
2                2013-01-18  48.846028,2.375429          Y2H15027244   
3                2013-01-18  48.846028,2.375429          Y2H15027244   
4                2013-01-18  48.846028,2.375429          Y2H15027244   

    latitude  ...  Rainfall (3h, mm)  Rainfall (6h, mm)  Rainfall (12h, mm)  \
0  48.846028  ...                0.0                0.0                 0.0   
1  48.846028  ...                0.0                0.0                 0.0   
2  48.846028  ...                0.0                0.0                 0.0   
3  48.846028  ...                0.0                0.0                 0.0   
4  48.846028  ...                0.0                0.0                 0.0   

  Rainfall (24h, mm)  Layer 1 Cloud Cover (oktas)  Layer 1 Cloud Type  \
0                0.0                          NaN                 NaN   
1                0.0                          2.0                 8.0   
2                0.0                          1.0                 8.0   
3                0.0                          NaN                 NaN   
4                0.0                          3.0                 6.0   

   Layer 1 Cloud Base Height (m)  Layer 2 Cloud Cover (oktas)  \
0                            NaN                          NaN   
1                         1700.0                          5.0   
2                         1700.0                          7.0   
3                            NaN                          NaN   
4                         1830.0                          5.0   

   Layer 2 Cloud Type  Layer 2 Cloud Base Height (m)  
0                 NaN                            NaN  
1                 6.0                         2300.0  
2                 6.0                         2400.0  
3                 NaN                            NaN  
4                 0.0                         8000.0  

[5 rows x 54 columns]

In [14]:
TableReport(merged_data)

Processing column  54 / 54


<TableReport: use .open() to display>

Decide to remove site id, site name and counter id to just keep counter name to reduce complexity and the data as they all provide more or less the same information. Counter is more precise as we will be able to calculate the number of times a counter is used in a given site.

## Model training with Elastic Net (To find the best features)

Elastic net can handle multicolinearity and shrinks the less important features to zero. It is a combination of L1 and L2 regularization. It is a linear regression model trained with L1 and L2 prior as regularizer. This combination allows for learning a sparse model where few of the weights are non-zero like Lasso, while still maintaining the regularization properties of Ridge.

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.linear_model import Lasso
from sklearn.linear_model import ElasticNet

# Define the features and target variable
X = merged_data.drop(columns=[
                            'bike_count', 'log_bike_count'
                            'count_id', 'site_id', 'site_name', 'counter_technical_id'
                            'coordinates',
                            'Station Number'
                    ])

y = merged_data['log_bike_count']

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Add a Lasso constraint on the model

# Create a pipeline with an imputer, standard scaler, and ElasticNet regression
elasticnet_pipeline = Pipeline([
    ('imputer', SimpleImputer(strategy='mean')),
    ('scaler', StandardScaler()),
    ('regressor', ElasticNet(alpha=0.1, l1_ratio=0.5))
])

# Fit the ElasticNet pipeline on the training data
elasticnet_pipeline.fit(X_train, y_train)

# Print the score of the ElasticNet model on the test data
print(f"ElasticNet model score: {elasticnet_pipeline.score(X_test, y_test)}")

# Output information about the ElasticNet model
elasticnet_coefficients = elasticnet_pipeline.named_steps['regressor'].coef_
elasticnet_feature_importance = pd.Series(elasticnet_coefficients, index=X.columns).sort_values(ascending=False)
print("ElasticNet feature importance:\n", elasticnet_feature_importance)

ValueError: Cannot use mean strategy with non-numeric data:
could not convert string to float: '100047548-104047548'

In [67]:
# Get the features with non-zero importance
non_zero_features = elasticnet_feature_importance[elasticnet_feature_importance != 0].index

# Filter the columns of X_train and X_test
merged_data_filtered = merged_data[non_zero_features]

# Display the filtered dataframes
merged_data_filtered.head()

Air Temperature (°C)   latitude  Total Cloud Cover (oktas)  Low Cloud Type  \
0                 10.95  48.846028                        0.0            30.0   
1                 20.65  48.846028                       60.0            38.0   
2                 19.15  48.846028                       90.0            38.0   
3                 19.75  48.846028                        NaN             NaN   
4                 27.35  48.846028                       75.0            35.0   

   10min Max Wind Gust (m/s)  Max Wind Gust (m/s)  Pressure Tendency (hPa/3h)  \
0                        1.5                  1.5                         -60   
1                        7.5                  7.5                        -110   
2                        6.5                  6.5                          10   
3                        3.7                  5.1                          60   
4                        7.7                  7.9                         -50   

   longitude  24h Pressure Tendency (hPa)  Present Weather Code  \
0   2.375429                          0.0                     2   
1   2.375429                       -260.0                     3   
2   2.375429                       -210.0                     2   
3   2.375429                        220.0                     0   
4   2.375429                        140.0                     3   

   Layer 2 Cloud Cover (oktas)  Layer 1 Cloud Cover (oktas)  Visibility (m)  \
0                          NaN                          NaN           25000   
1                          5.0                          2.0           30000   
2                          7.0                          1.0           30000   
3                          NaN                          NaN           49310   
4                          5.0                          3.0           30000   

   New Snowfall Duration (hours)  Relative Humidity (%)  
0                          -30.0                     88  
1                          -30.0                     41  
2                          -60.0                     47  
3                            NaN                     44  
4                          -30.0                     36

In [ ]:
# Subtract 273 from all values in the "Air Temperature (°C)" column
merged_data_filtered.loc[:,'Air Temperature (°C)'] -= 273
merged_data_filtered.head()

In [68]:
merged_data_filtered

Air Temperature (°C)   latitude  Total Cloud Cover (oktas)  \
0                      10.95  48.846028                        0.0   
1                      20.65  48.846028                       60.0   
2                      19.15  48.846028                       90.0   
3                      19.75  48.846028                        NaN   
4                      27.35  48.846028                       75.0   
...                      ...        ...                        ...   
165363                 29.95  48.839770                       40.0   
165364                 20.55  48.839770                       90.0   
165365                 17.45  48.839770                       40.0   
165366                 19.85  48.839770                      100.0   
165367                 26.35  48.839770                       75.0   

        Low Cloud Type  10min Max Wind Gust (m/s)  Max Wind Gust (m/s)  \
0                 30.0                        1.5                  1.5   
1                 38.0                        7.5                  7.5   
2                 38.0                        6.5                  6.5   
3                  NaN                        3.7                  5.1   
4                 35.0                        7.7                  7.9   
...                ...                        ...                  ...   
165363            30.0                       11.4                 12.5   
165364            39.0                        4.9                 12.1   
165365            30.0                        3.7                  3.7   
165366            32.0                        4.3                  5.4   
165367            38.0                        8.5                  9.7   

        Pressure Tendency (hPa/3h)  longitude  24h Pressure Tendency (hPa)  \
0                              -60   2.375429                          0.0   
1                             -110   2.375429                       -260.0   
2                               10   2.375429                       -210.0   
3                               60   2.375429                        220.0   
4                              -50   2.375429                        140.0   
...                            ...        ...                          ...   
165363                        -220   2.301980                       -400.0   
165364                          60   2.301980                        150.0   
165365                         -90   2.301980                       -800.0   
165366                         -10   2.301980                       -230.0   
165367                         -70   2.301980                         80.0   

        Present Weather Code  Layer 2 Cloud Cover (oktas)  \
0                          2                          NaN   
1                          3                          5.0   
2                          2                          7.0   
3                          0                          NaN   
4                          3                          5.0   
...                      ...                          ...   
165363                     3                          NaN   
165364                    25                          2.0   
165365                     3                          NaN   
165366                    10                          NaN   
165367                     2                          4.0   

        Layer 1 Cloud Cover (oktas)  Visibility (m)  \
0                               NaN           25000   
1                               2.0           30000   
2                               1.0           30000   
3                               NaN           49310   
4                               3.0           30000   
...                             ...             ...   
165363                          3.0           12670   
165364                          4.0           48430   
165365                          3.0           19860   
165366                          7.0            5000   
165